# Previsão de renda

### 4 elementos importantes
- Esse notebook
- Streamlit com as análises
- Seu Github com o projeto
- Vídeo no readme do github mostrando o streamlit

## Etapa 1 CRISP - DM: Entendimento do negócio

<span style="color:red">O objetivo deste projeto é desenvolver um modelo de previsão de renda de clientes com base em características sociais e profissionais. 
A previsão de renda é uma informação estratégica para instituiçãoes financeiras ,  pois auxilia na tomada de decisão relacionada á concessão de crédito , definição de limites e análise de futuros riscos </span>


## Etapa 2 Crisp-DM: Entendimento dos dados
<span style="color:red"> O conjunto dos dados contém informações cadastrais e socioeconômicas de clientes , incluido variáveis demográficas , situação familiar, características profissionais e renda </span>


### Dicionário de dados

<span style="color:red"> </span>


| Variável                | Descrição                                           | Tipo         |
| ----------------------- |:---------------------------------------------------:| ------------:|
| id_ref                  |  Data de referência do registro do cliente .        |  Data        |
|  id_cliente             |   identificador único do cliente                    | numérica     |
| sexo                    |  Sexo do cliente (genêro)                           | Categórica   |
| posse_de_veiculo        |  indica se o cliente possui ou não veículo          | Categórica   |
| posse_de_imovel         |  indica se o cliente possui ou não imóvel           | Categórica   |
| qtd_filhos              |  Quantidade de filhos do cliente                    | numérica     |
| tipo_renda              |  tipo de renda do cliente                           | Categórica   |
| educacao                |  Nível de escolaridade do cliente                   | Categórica   |
| estado_civil            |  Estado civil do cliente                            | Categórica   |
| tipo_residencia         |  Tipo de residência onde o cliente mora             | Categórica   |
| idade                   |  idade so cliente em anos                           | numérica     |
| tempo_emprego           |  tempo de permanência do cliente no emprego atual   | numérica     |  
| qt_pessoas_residencia   |  quantidades de pessoas que residem no mesma casa   | numérica     |                                             | renda                   |  renda mensal do cliente                            | numérica     |                






#### Carregando os pacotes
É considerado uma boa prática carregar os pacotes que serão utilizados como a primeira coisa do programa.

#### Carregando os dados
O comando pd.read_csv é um comando da biblioteca pandas (pd.) e carrega os dados do arquivo csv indicado para um objeto *dataframe* do pandas.

In [1]:
import pandas as pd
import seaborn as sns
import matplotlib.pyplot as plt
from ydata_profiling import ProfileReport
import os
import numpy as np
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LinearRegression
from sklearn.metrics import mean_absolute_error, mean_squared_error, r2_score
from sklearn.preprocessing import StandardScaler
from sklearn.ensemble import RandomForestRegressor
from sklearn.preprocessing import OneHotEncoder , StandardScaler
from sklearn.compose import ColumnTransformer
from sklearn.pipeline import Pipeline
import joblib
from pathlib import Path
from sklearn.linear_model import Ridge

In [2]:
#carregando o dataset
renda = pd.read_csv("../dataset/previsao_de_renda.csv")
renda.head(1)

Unnamed: 0    data_ref  id_cliente sexo  posse_de_veiculo  posse_de_imovel  \
0           0  2015-01-01       15056    F             False             True   

   qtd_filhos  tipo_renda    educacao estado_civil tipo_residencia  idade  \
0           0  Empresário  Secundário     Solteiro            Casa     26   

   tempo_emprego  qt_pessoas_residencia    renda  
0        6.60274                    1.0  8060.34

#### Entendimento dos dados - Univariada
Nesta etapa tipicamente avaliamos a distribuição de todas as variáveis. 

In [3]:
prof = ProfileReport(renda, explorative=True )
prof


Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

100%|██████████| 15/15 [00:00<00:00, 187.67it/s]


Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

<span style="color:red">O Dataset possui 15 colunas e 15.000 observações representando registros individuais de clientes  também observa-se uma baixa proporção de valores ausentes cerca de 1,1% o que indica uma boa qualidade geral dos dados

Variáveis numéricas:
* renda 
* idade
* tempo_emprego 

Variáveis categóricas:
* sexo
* educacao
* estado_civil

variaveis booleanas :
* posse_de_imovel / posse_de_veiculo

Na análise univariada , avaliamos o comportamento individual das variáveis do conjunto de dados. O Dataset apresenta boa qualidade geral , com apenas cerca de 1,1% de valores ausentes. As variáveis numéricas , como renda, idade e tempo de emprego  apresentam distribuições assimétricas, especialemente a renda  que possui concentração em valores mais  baixos  e presença de valores extremos .
variáveis categóricas como sexo , estado civil e educação apresentam poucas categorias bem definidas e sem valores faltantes , indicando consistência mnos dados.</span>


### Entendimento dos dados - Bivariadas




<span style="color:red">baseando-nos na matriz de  correlação , indica que não há correlações lineares fortes entre variáveis explicativas , reduzindo o risco de multicolinearidade no modelo . podemos ver que há correlações positivas moderadas entre qtd_filhos e qtd_pessoas_residencia, assim como entre tempo_emprego e renda  , relações  esperadas do ponto de vista  socieconômico . variáveis como posse de veiculo e imóvel apresentam  associação positiva  leve com a renda , sugerindo potencial explicativo. </span>


## Etapa 3 Crisp-DM: Preparação dos dados
Nessa etapa realizamos tipicamente as seguintes operações com os dados:

 - **seleção**: Já temos os dados selecionados adequadamente?
 - **limpeza**: Precisaremos identificar e tratar dados faltantes
 - **construção**: construção de novas variáveis
 - **integração**: Temos apenas uma fonte de dados, não é necessário integração
 - **formatação**: Os dados já se encontram em formatos úteis?



In [4]:
print(renda.shape) #total de linhas e colunas antes da remoção

(15000, 15)


In [5]:
df = renda.copy() #copia do dataset original 
coluna_remove = ['Unnamed: 0', 'id_cliente' , 'data_ref']
df.drop(columns=coluna_remove, inplace=True)
df.head(2)

sexo  posse_de_veiculo  posse_de_imovel  qtd_filhos   tipo_renda  \
0    F             False             True           0   Empresário   
1    M              True             True           0  Assalariado   

            educacao estado_civil tipo_residencia  idade  tempo_emprego  \
0         Secundário     Solteiro            Casa     26       6.602740   
1  Superior completo       Casado            Casa     28       7.183562   

   qt_pessoas_residencia    renda  
0                    1.0  8060.34  
1                    2.0  1852.15

 Variáveis identificadoras e temporais foram removidas por não contribuirem diretamente para predição da renda .

In [6]:
print(df.shape) #total de linhas e colunas após a remoção

(15000, 12)


<span style="color:red">Nesta etapa foram removidas variáveis identificadoras e téncinas que não possuem poder explicativo para o modelo</span>

observamos que a variável tempo emprego apresentou maior valume de valores ausentes e foi imputada pela mediana por ser mais robusta a outliers.

In [7]:
df['tempo_emprego'] = df['tempo_emprego'].fillna(df['tempo_emprego'].median())

In [8]:
#construção de novas variáveis
df = df.assign(
    possui_bens=(
    (df['posse_de_veiculo'] == 1) |
    (df['posse_de_imovel'] > 0)
).astype(int)
    
)

In [9]:
df[['posse_de_veiculo', 'posse_de_imovel', 'possui_bens']].head(5)

posse_de_veiculo  posse_de_imovel  possui_bens
0             False             True            1
1              True             True            1
2              True             True            1
3             False             True            1
4              True            False            1

foi criada a variavel possui_bens , combinando informações de posse de imóvel e veículo, com o objetivo de representar de forma mais direta o patrimônio do indivíduo 


<span style="color:red">Integração dos dados</span>

O projeto utiliza apenas uma única fonte de dados , não sendo necessária a etapa de integração.

In [10]:
#formatação dos dados
#convertendo variáveis categóricas em numéricas
colunas_categoricas = ['sexo', 'educacao', 'estado_civil', 'tipo_residencia','tipo_renda']
for coluna in colunas_categoricas:
    df[coluna] = df[coluna].astype('category')
    
colunas_booleanas = ['posse_de_veiculo' , 'posse_de_imovel','possui_bens']
for coluna in  colunas_booleanas:
    df[coluna] = df[coluna].astype(int)
    
df.dtypes

sexo                     category
posse_de_veiculo            int64
posse_de_imovel             int64
qtd_filhos                  int64
tipo_renda               category
educacao                 category
estado_civil             category
tipo_residencia          category
idade                       int64
tempo_emprego             float64
qt_pessoas_residencia     float64
renda                     float64
possui_bens                 int64
dtype: object

## Etapa 4 Crisp-DM: Modelagem
Nessa etapa que realizaremos a construção do modelo. Os passos típicos são:
- Selecionar a técnica de modelagem
- Desenho do teste
- Avaliação do modelo


<span style="color:red">Nesta etapa foi selecionada tecnica de regressão , uma vez que o objetivo do projeto é prever um valor numérico contínuo , no caso a rend\ dos clientes.  A regressão linear é a melhor opção por sua simplicidade  , interpretabilidade e adequação como baseline para comparação com modelos mais complexos .</span>


### Rodando o modelo


<span style="color:red"> O conjunto dos dados foi divido em conjuntos de treinamentos e testes , permitindo avaliar a capacidade  de generalização  do moelo em dados não vistos </span>

In [11]:
x = df.drop(columns=['renda'])
y = df['renda']

In [12]:
#divisão dos dados em treinos e testes 


x_train , x_test , y_train ,y_test =  train_test_split(  
    x , y , test_size=0.2 , random_state=42
)

In [13]:
num_cols = x.select_dtypes(include=['int64', 'float64']).columns
cat_cols = x.select_dtypes(include=['category']).columns
bin_cols = x.select_dtypes(include=['bool']).columns

In [14]:
preprocess = ColumnTransformer(
    transformers=[
        ("num", StandardScaler(), num_cols),
        ("cat" , OneHotEncoder(handle_unknown="ignore"), cat_cols),
        ("bin" , OneHotEncoder(drop='if_binary'), bin_cols)
    ],
    remainder='drop'
)

In [15]:
ridge = Ridge(alpha=1.0)


In [16]:
pipeline_ridge = Pipeline(
    steps=[
        ('preprocess', preprocess),
        ('ridge', Ridge(alpha=1.0))
])
pipeline_ridge.fit(x_train , y_train)

Pipeline(steps=[('preprocess',
                 ColumnTransformer(transformers=[('num', StandardScaler(),
                                                  Index(['posse_de_veiculo', 'posse_de_imovel', 'qtd_filhos', 'idade',
       'tempo_emprego', 'qt_pessoas_residencia', 'possui_bens'],
      dtype='object')),
                                                 ('cat',
                                                  OneHotEncoder(handle_unknown='ignore'),
                                                  Index(['sexo', 'tipo_renda', 'educacao', 'estado_civil', 'tipo_residencia'], dtype='object')),
                                                 ('bin',
                                                  OneHotEncoder(drop='if_binary'),
                                                  Index([], dtype='object'))])),
                ('ridge', Ridge())])

In [17]:
#avaliação do modelo 
y_pred = pipeline_ridge.predict(x_test)
mea = mean_absolute_error(y_test , y_pred)
rmse = np.sqrt(mean_squared_error(y_test , y_pred))
r2 = r2_score(y_test , y_pred)

mea , rmse , r2

(3491.226289825856, np.float64(5872.33340731146), 0.29624008251390677)

## Etapa 5 Crisp-DM: Avaliação dos resultados


In [18]:
#tratando a variável alvo(renda)
#transformação logarítmica 
df['renda_log']  = np.log1p(df['renda'])

y = df['renda_log']


A transformação logarítimica foi aplicada para reduzir a assimetria da distribuição da renda e minimizar o impacto de valores extremos 

In [19]:
#fazendo encoding das variaveis categóricas
x = df.drop(columns=['renda' , 'renda_log'])
y = df['renda_log']




In [20]:
df.columns

Index(['sexo', 'posse_de_veiculo', 'posse_de_imovel', 'qtd_filhos',
       'tipo_renda', 'educacao', 'estado_civil', 'tipo_residencia', 'idade',
       'tempo_emprego', 'qt_pessoas_residencia', 'renda', 'possui_bens',
       'renda_log'],
      dtype='object')

In [21]:
num_cols = ['idade' , 'qtd_filhos' , 'qt_pessoas_residencia']
bin_cols = ['sexo' , 'posse_de_imovel' , 'posse_de_veiculo']
cat_cols = ['educacao' , 'estado_civil' , 'tipo_residencia' ]

In [22]:
x_train , x_test , y_train ,y_test =  train_test_split(  
    x , y , test_size=0.2 , random_state=42
)

In [23]:
preprocess = ColumnTransformer(
    transformers=[
        ("num", StandardScaler() , num_cols) ,
        ("bin", OneHotEncoder(), bin_cols),
        ("cat", OneHotEncoder(handle_unknown="ignore"), cat_cols)
    ]
)

In [24]:
pipeline_rf= Pipeline(
    steps=[
        ("preprocess" , preprocess),
        ("model" , RandomForestRegressor(
            n_estimators=300,
            random_state=42,
            n_jobs=1
        ))
    ]
)

In [25]:
pipeline_rf.fit(x_train , y_train)

Pipeline(steps=[('preprocess',
                 ColumnTransformer(transformers=[('num', StandardScaler(),
                                                  ['idade', 'qtd_filhos',
                                                   'qt_pessoas_residencia']),
                                                 ('bin', OneHotEncoder(),
                                                  ['sexo', 'posse_de_imovel',
                                                   'posse_de_veiculo']),
                                                 ('cat',
                                                  OneHotEncoder(handle_unknown='ignore'),
                                                  ['educacao', 'estado_civil',
                                                   'tipo_residencia'])])),
                ('model',
                 RandomForestRegressor(n_estimators=300, n_jobs=1,
                                       random_state=42))])

In [26]:
y_pred_log = pipeline_rf.predict(x_test)
y_pred_reais = np.expm1x(y_pred_log)



mea = mean_absolute_error(y_test , y_pred_reais)
rmse = np.sqrt(mean_squared_error(y_test , y_pred_reais))
r2 = r2_score(y_test , y_pred_reais)

mea , rmse , r2

(4525.017809274504, np.float64(5887.702890960499), -45328619.061016545)

<span style="color:red"> A regressão Ridge foi aplicada como uma abordagem linear regularizada, com o objetivo de reduzir a variância do modelo e mitigar possíveis efeitos de multicolinearidade entre as variáveis explicativas. A regularização L2 imposta pelo Ridge penaliza coeficientes excessivamente elevados, contribuindo para maior estabilidade numérica e melhor capacidade de generalização.

Resultados obtidos:
	MAE: ~ R$ 3.491,
	RMSE: ~ R$ 5.872,
	R²: ~ 0.296,

Esses resultados indicam que o modelo consegue capturar uma parcela relevante da variabilidade da renda, mantendo erro médio absoluto relativamente menor em comparação ao modelo alternativo testado. O comportamento do Ridge mostrou-se consistente no conjunto de teste, sem sinais de degradação severa ou overfitting.</span>

O Random Forest Regressor foi empregado como um modelo não linear baseado em múltiplas árvores de decisão, capaz de capturar interações complexas entre as variáveis. Para lidar com a assimetria da variável alvo, foi aplicada uma transformação logarítmica na renda, seguida de reconversão para a escala original após a previsão.

Resultados obtidos (após reconversão para reais):
	•	MAE: ~ R$ 4.525
	•	RMSE: ~ R$ 5.887
	•	R²: ~ –0.45

Apesar de apresentar boa capacidade de aprendizado no espaço logarítmico, o modelo não conseguiu traduzir esses ganhos em previsões precisas na escala original da renda. O R² negativo indica desempenho inferior a uma estratégia simples baseada na média, evidenciando dificuldades de generalização para valores absolutos em reais.

In [27]:
Path("app/models").mkdir(parents=True, exist_ok=True)
joblib.dump(pipeline_ridge, '../app/models/ridge_model.pk1')

['../app/models/ridge_model.pk1']

## Etapa 6 Crisp-DM: Implantação
Nessa etapa colocamos em uso o modelo desenvolvido, normalmente implementando o modelo desenvolvido em um motor que toma as decisões com algum nível de automação.